In [1]:
import pandas as pd 
import plotly.express as px
import numpy as np
import pysam

def count_mapped_reads(bam_file):
    mapped_reads = 0
    # Open the BAM file
    with pysam.AlignmentFile(bam_file, "rb") as bam:
        # Iterate over alignments
        for alignment in bam:
            # Check if the alignment is mapped
            if not alignment.is_unmapped:
                mapped_reads += 1

    return mapped_reads

In [2]:
metadata_path = "../../config/metadata_ms.tsv"
wkdir = "../.."

In [3]:
# Parameters
wkdir = "/home/snagi/lstm_projects/ampseq-agvampir002"
metadata_path = "config/metadata_ms.tsv"


# Plate statistics

In this notebook, we explore how sample-level statistics look when we map out the sample by their position on a plate. 
First, lets explore a histogram of the overall reads per sample. 

In [4]:
def extract_percentage(string):
    import re
    # Pattern to match a percentage value
    pattern = r'(\d+(?:\.\d+)?)%'
    # Search for the pattern in the string
    match = re.search(pattern, string)
    if match:
        percentage = float(match.group(1))
        return percentage
    return None

if metadata_path.endswith('.xlsx'):
    metadata = pd.read_excel(metadata_path, engine='openpyxl')
elif metadata_path.endswith('.tsv'):
    metadata = pd.read_csv(metadata_path, sep="\t")
elif metadata_path.endswith('.csv'):
    metadata = pd.read_csv(metadata_path, sep=",")
else:
    raise ValueError("Metadata file must be .xlsx or .csv")

# count mapped reads in bams 
mapped_reads = []
freq_mapped = []
for sample_id in metadata['sample_id']:
    # Call the count_mapped_reads function
    mapped_reads_count = count_mapped_reads(f"{wkdir}/results/alignments/{sample_id}.bam")
    mapped_reads.append(mapped_reads_count)
    
    df = pd.read_csv(f"{wkdir}/results/alignments/bamStats/{sample_id}.flagstat")
    freq_mapped.append(extract_percentage(df.iloc[6, 0]))

In [5]:
metadata = metadata.assign(mapped_reads=mapped_reads, freq_mapped=freq_mapped)
metadata = metadata.drop(columns=['latitude', 'longitude', 'taxon'], errors='ignore')

fig = px.histogram(metadata, x='mapped_reads', nbins=60, width=600, height=400, template='simple_white')
fig

### Mapped reads per well

The below plot displays the samples in their 96 well plate format, showing the number of mapped reads assigned to each sample. Extra data on each sample is available by hovering over the wells. 

In [6]:
def plot_96well_plate(metadata, range_color=None, color_var='mapped_reads', title='Plate A - Number of mapped reads'):
    fig = px.scatter(metadata[::-1], 
                     y='well_letter', 
                     x='well_number',
                     color=color_var, 
                     hover_data=metadata.columns,
                     range_color=range_color,
                     template='plotly_white',
                      width=850,
                      height=550
                     )
    fig.update_traces(marker_size=30)
    fig.update_layout(xaxis = dict(
                                side='top',
                                tickmode = 'linear',
                                tick0 = 0,
                                dtick = 1), 
                                xaxis_range=[0, 12.5],
                      title=title,
                        yaxis_title="Well Letter",
                        xaxis_title="Well Number",
                      )
    fig.layout.xaxis.automargin = True
    return fig

for plate in metadata.plate.unique():
    df = metadata.query(f"plate == @plate")
    fig = plot_96well_plate(df, range_color=(0, 20000), color_var='mapped_reads', title=f'Plate {plate} - Number of mapped reads')
    fig.show()

In [7]:
for plate in metadata.plate.unique():
    df = metadata.query(f"plate == @plate")
    fig = plot_96well_plate(df, range_color=(0,100), color_var='freq_mapped', title=f'Plate {plate} - % of reads that align to reference')
    fig.show() 